# <center> Energy balance models </center>

# Table of contents

1. [Introduction](#introduction) <br>
2. [Preparation](#preparation) <br>
3. [Idealized sea ice EBM (Aquaplanet)](#seaiceebm) <br>
    3.1 [General](#general_si) <br>
    3.2 [Functions](#sifunctions)
4. [Temperature EBM](#tebm) <br>
    4.1 [General](#generaltebm) <br>
    4.2 [Functions](#tebmfunctions)<br>
5. [Try it out](#widget) <br>
6. [Testing area](#testing) <br>

# 1. Introduction

"Previous studies identified instabilities for a shrinking ice cover in two types of idealized climate models: (i) annual-mean latitudinally varying diffusive energy balance models (EBMs) and (ii) seasonally varying single-column models (SCMs). The instabilities in these low-order models stand in contrast with results from compre- hensive global climate models (GCMs), which typically do not simulate any such instability. To help bridge the gap between low-order models and GCMs, an idealized model is developed that includes both latitudinal and seasonal variations. The following EBM is a idealized representation of sea ice and climate with seasonal and latitudinal variations in a global domain." <i>(Extraced from: Till J.W Wagner and Ian Eisenman, "How Climate Model Complexity Influences Sea Ice Stability" (2015) p.2 Abstract)</i>
> [Paper and Documentation](https://www.researchgate.net/publication/276276426_How_Climate_Model_Complexity_Influences_Sea_Ice_Stability)

> [Source code](http://eisenman.ucsd.edu/code.html)


# 2. Preparation <a name="preparation"></a>

In [1]:
import numpy as np
import matplotlib.pyplot as plt
import tqdm as tqdm
from ipywidgets import *

import warnings
warnings.filterwarnings('ignore')

import seaborn as sns
sns.set_style("white")

# 3. Idealized sea sce EBM (Aquaplanet) <a name="seaiceebm"></a>
## Sea Ice EBM calculation

In [46]:
#D = 0.6 # diffusivity for heat transport (W m^-2 K^-1) | typical range: 0.44 - 0.66
#S1 = 338; # insolation seasonal dependence (W m^-2)
#A = 193 # OLR when T = T_m (W m^-2)
#B = 2.1 # OLR temperature dependence (W m^-2 K^-1)
#cw = 9.8 # ocean mixed layer heat capacity (W yr m^-2 K^-1) | Wärmekapazität der gemischten Ozeanschicht
#S0 = 420 # insolation at equator (W m^-2)
#S2 = 240 # insolation spatial dependence (W m^-2)
#a0 = 0.7 # ice-free coalbedo at equator
#a2 = 0.1 # ice-free coalbedo spatial dependence
#ai = 0.4 # co-albedo where there is sea ice
#Fb = 4; # heat flux from ocean below (W m^-2)
#k = 2; # sea ice thermal conductivity (W m^-2 K^-1)
#Lf = 9.5; # sea ice latent heat of fusion (W yr m^-3) | latente Schmelzwärme von Meereis
#cg = 0.01*cw; # ghost layer heat capacity(W yr m^-2 K^-1)
#tau = 1e-5; # ghost layer coupling timescale (yr)
#D=0.6,S1=338,A=193,B=2.1,cw=9.8,S0=420,S2=240,a0=0.7,a2=0.1,ai=0.4,Fb=4,k=2,Lf=9.5,cg=0.01,tau=1e-5, winter=26, summer=76
#winter = 26 #time of coldest <T>
#summer = 76 #time of warmest <T>

def calculationSeaIce(D=0.6, S1=338, A=193, B=2.1, cw=9.8, S0=420, S2=240, 
                a0=0.7, a2=0.1, ai=0.4, Fb=4, k=2, Lf=9.5, cg=0.01,
                tau=1e-5, winter=26, summer=76, years=30):

    cg*=cw
    
    ##The default run in WE15, Fig 2 uses the time-stepping parameters: -------
    #n=400; % # of evenly spaced latitudinal gridboxes (equator to pole)
    #nt=1e3; % # of timesteps per year (approx lower limit of stability)
    #dur=200; % # of years for the whole run
    ##For a quicker computation, use the parameters: --------------------------
    n = 100;  nt = 1e3;
    dur= years #30;
    dt = 1/nt;
    #Spatial Grid -------------------------------------------------------------
    dx = 1.0/n #grid box width
    x = np.arange(dx/2,1+dx/2,dx) #native grid
    xb = np.arange(dx,1,dx)
    ##Diffusion Operator (WE15, Appendix A) -----------------------------------
    lam = D/dx**2*(1-xb**2)
    L1=np.append(0, -lam); L2=np.append(-lam, 0); L3=-L1-L2
    diffop = - np.diag(L3) - np.diag(L2[:n-1],1) - np.diag(L1[1:n],-1);
    ##Definitions for implicit scheme on Tg
    cg_tau = cg/tau;
    dt_tau = dt/tau;
    dc = dt_tau*cg_tau;
    kappa = (1+dt_tau)*np.identity(n)-dt*diffop/cg;
    ##Seasonal forcing (WE15 eq.3)
    ty = np.arange(dt/2,1+dt/2,dt)
    S = (np.tile(S0-S2*x**2,[int(nt),1])-
    np.tile(S1*np.cos(2*np.pi*ty),[n,1]).T*np.tile(x,[int(nt),1]));
    ##Further definitions
    M = B+cg_tau;
    aw = a0-a2*x**2 # open water albedo
    kLf = k*Lf;
    #Set up output arrays, saving 100 timesteps/year
    E100 = np.zeros([n,dur*100]); T100 = np.zeros([n,dur*100])
    p = -1; m = -1
    #Initial conditions ------------------------------------------------------
    T = 7.5+20*(1-2*x**2);
    Tg = T; E = cw*T;
    #Integration (see WE15_NumericIntegration.pdf)----------------------------
    #Loop over Years ---------------------------------------------------------
    info.clear_output()
    with info:
        for years in tqdm.tqdm(range(0,dur)):
            #Loop within One Year-------------------------------------------------
            for i in range(0, int(nt)):
                m = m+1
                #store 100 timesteps per year
                if (p+1)*10 == m:
                    p = p+1
                E100[:,p] = E
                T100[:,p] = T
                #forcing
                alpha = aw*(E>0) + ai*(E<0) #WE15, eq.4
                C = alpha*S[i,:]+cg_tau*Tg-A
                #surface temperature
                T0 = C/(M-kLf/E) #WE15, eq.A3
                T = E/cw*(E>=0)+T0*(E<0)*(T0<0); #WE15, eq.9
                #Forward Euler on E
                E = E+dt*(C-M*T+Fb); #WE15, eq.A2
                #Implicit Euler on Tg
                Tg = np.linalg.solve(kappa-np.diag(dc/(M-kLf/E)*(T0<0)*(E<0)),
                Tg+(dt_tau*(E/cw*(E>=0)+(ai*S[i,:]-A)/(M-kLf/E)*(T0<0)*(E<0))))
            #print('year %d complete' %(years))
    #-------------------------------------------------------------------------
    #output only converged, final year
    tfin = np.linspace(0,1,100)
    Efin = E100[:,-101:-1]
    Tfin = T100[:,-101:-1]
    # ------------------------------------------------------------------------
    #WE15, Figure 2: Default Steady State Climatology ------------------------
    # ------------------------------------------------------------------------
    winter = 26 #time of coldest <T>
    summer = 76 #time of warmest <T>
    
    #compute seasonal ice edge
    xi = np.zeros(100)
    #if isempty(find(E<0,1))==0:  
    for j in range(0,len(tfin)):
        E = Efin[:,j]
        if any(E<0):
            ice = np.where(E<0)[0]
            xi[j] = x[ice[0]];
        else:
            xi[j] = max(x);

    return x, xi, tfin, Tfin, Efin, Lf, winter, summer

### Sea Ice EBM plot function

In [47]:
def plot_SeaIce_result(x, xi, tfin, Tfin, Efin, Lf, winter, summer, f):
    
    cmap=plt.cm.RdBu_r
    summer_color="red"
    winter_color="skyblue"
    
    #plot enthalpy (Fig 2a)
    axarr1 = f.add_subplot(141)
    clevsE = np.append(np.arange(-40,20,20), np.arange(50,350,50))
    plt.contourf(tfin, x, Efin, clevsE, cmap=cmap) #plt.contourf(tfin, x90deg, Efin, clevsE, cmap=cmap) 
    plt.colorbar()#label=r"$E(Jm^{-2})$")
    #plot ice edge on E
    plt.plot(tfin, xi,'k'); #plt.plot(tfin, xi90deg,'k')
    plt.xlabel('t (final year)')
    plt.ylabel('x')
    plt.title(r'$a)$ $E(J\;m^{-2})$')
    
    #plot temperature (Fig 2b)
    axarr2 = f.add_subplot(142)
    clevsT = np.arange(-30.001, 35., 5.)
    plt.contourf(tfin, x, Tfin, clevsT, cmap=cmap) #plt.contourf(tfin, x90deg, Tfin, clevsT, cmap=cmap) #
    plt.colorbar()#label=r"$T(...$")
    #plot ice edge on T
    plt.plot(tfin, xi,'k', color="black") #plt.plot(tfin, np.arcsin(xi)*180/np.pi,'k')
    #plot T=0 contour (the region between ice edge and T=0 contour is the
    #region of summer ice surface melt)
    plt.contour(tfin, x, Tfin, [-0.001], colors='r', linestyles='-') #plt.contour(tfin, x90deg, Tfin, [-0.001], colors='r', linestyles='-')
    plt.xlabel('t (final year)')
    plt.ylabel('x') #x
    plt.title(r'$b)$ T($^\circ$C)')

    #plot the ice thickness (Fig 2c)
    axarr3 = f.add_subplot(1, 4, 3)
    clevsh = np.arange(0.00001, 4.5, .5)
    hfin = -Efin/Lf*(Efin<0)
        
    plt.contourf(tfin, x, hfin, clevsh, cmap="Blues") #plt.contourf(tfin, x90deg, hfin, clevsh, cmap="Blues")
    plt.colorbar()
    #plot ice edge on h
    plt.contour(tfin, x, hfin,[0],colors='k') # plt.contour(tfin, x90deg, hfin,[0],colors='k')
    plt.plot([tfin[winter], tfin[winter]], [0,max(x)], 'k', color=winter_color) # plt.plot([tfin[winter], tfin[winter]], [0,max(np.arcsin(x)*170/np.pi)], 'k')
    plt.plot([tfin[summer], tfin[summer]], [0,max(x)], 'k--', color=summer_color) #plt.plot([tfin[summer], tfin[summer]], [0,max(np.arcsin(x)*170/np.pi)], 'k--')
    plt.xlabel('t (final year)')
    plt.ylabel('x')
    plt.title('$c)$ Sea ice thickness $h(m)$')

    #plot temperature profiles (Fig 2d)
    axarr4 = f.add_subplot(444)
    Summer, = plt.plot(x, Tfin[:,summer], 'k--', label='summer', color=summer_color) #Summer, = plt.plot(x90deg, Tfin[:,summer], 'k--', label='summer')
    Winter, = plt.plot(x, Tfin[:,winter], 'k', label='winter', color=winter_color) #Winter, = plt.plot(x90deg, Tfin[:,winter], 'k', label='winter')
    plt.plot([0,1], [0,0], 'k', linewidth=0.7) #plt.plot([0,x90deg.max()], [0,0], 'k')
    plt.xlabel('x') 
    plt.ylabel('T ($^\circ$C)')
    plt.title('$d)$ Surface temperature')
    plt.legend(handles = [Summer,Winter],loc=0)

    #plot ice thickness profiles (Fig 2e)
    axarr5 = f.add_subplot(448)
    plt.plot(x, hfin[:, summer],'k--', color=summer_color) #plt.plot(x90deg, hfin[:, summer],'k--')
    plt.plot(x, hfin[:, winter],'k',color=winter_color) # plt.plot(x90deg, hfin[:, winter],'k')
    plt.plot([0,1], [0,0],'k', linewidth=0.7) #plt.plot([0,x90deg.max()], [0,0],'k')
    plt.xlim([0.7, 1]) #plt.xlim([x90deg.max()*0.7,x90deg.max()])
    plt.xlabel('x')
    plt.ylabel('$h(m)$')
    plt.title('$e)$ Ice thickness $h$ where $0.7 < x < 1$')
    plt.legend(handles = [Summer,Winter],loc=0)

    #plot seasonal thickness cycle at pole (Fig 2f)
    axarr6 = f.add_subplot(4, 4, 12)
    plt.plot(tfin, hfin[-1,:], 'k')
    plt.xlabel('t (yr)')
    plt.ylabel('h$_p(m)$')
    plt.ylim([2, 1.1*max(hfin[-1,:])])
    plt.title('$f)$ seas. cycle of ice thickness at the pole $h_p$')

    #plot ice edge seasonal cycle (Fig 2g)
    axarr7 = f.add_subplot(4, 4, 16)
    xideg = np.degrees(np.arcsin(xi));
    plt.plot(tfin, xideg,'k-')
    plt.ylim([0, 90])
    plt.xlabel('t (yr)')
    plt.ylabel(r'$\theta_i$ (deg)')
    plt.title(r'$g)$ seas. cycle of the lat. of sea ice edge $\omega_{i}$')
    plt.tight_layout()
    return f

### Sea Ice EBM widget settings

In [48]:
style = {'description_width': '440px'}
layout = {'width': '525px'}

D_inp = widgets.FloatText(description='Diffusivity for heat transport ($D^{*} = Wm^{-2}K^{-1}$):',
                                 value=0.6, style=style, layout=layout)
S1_inp = widgets.FloatText(description='Insolation seasonal dependence ($S^{*}_{1} = Wm^{-2}$):',
                                  value=338, max=float('inf'), style=style, layout=layout)
A_inp = widgets.FloatText(description='OLR when $T=T_m$ ($ A = Wm^{-2}$):',
                                 value=193, max=float('inf'), style=style, layout=layout)
B_inp = widgets.FloatText(description='OLR temperature dependence ($B = Wm^{-2}K^{-1}$):',
                                 value=2.1, style=style, layout=layout)
cw_inp = widgets.FloatText(description='Ocean mixed layer heat capacity ($c_{w} = W\;yr\;m^{-2}K^{-1}$):',
                                  value=9.8, style=style, layout=layout)
S0_inp = widgets.FloatText(description='Insolation at equator ($S_{0} = Wm^{-2}$):',
                                  value=420, max=float('inf'), style=style, layout=layout)
S2_inp = widgets.FloatText(description='Insolation spatial dependence ($S_{2} = Wm^{-2}$):',
                                  value=240, max=float('inf'), style=style, layout=layout)
a0_inp = widgets.FloatText(description='Ice-free coalbedo at equator ($A_0$):',
                                  value=0.7, style=style, layout=layout)
a2_inp = widgets.FloatText(description='Ice-free coalbedo spatial dependence ($A_{2}$):',
                                  value=0.1, style=style, layout=layout)
ai_inp = widgets.FloatText(description='Coalbedo where is sea ice ($a_{i}$):',
                                  value=0.4, style=style, layout=layout)
Fb_inp = widgets.FloatText(description='Heat flux from ocean below ($F_{b} = Wm^{-2}$):',
                                  value=4, style=style, layout=layout)
k_inp = widgets.FloatText(description='Sea ice thermal conductivity ($K = Wm^{-2}K^{-1}$):',
                                 value=2, style=style, layout=layout)
Lf_inp = widgets.FloatText(description='Sea ice latent heat of fusion ($L_{f} = W\;yr\;m^{-3}$):',
                                  value=9.5, style=style, layout=layout)
cg_inp = widgets.FloatText(description='Ghost layer heat capacity($c_{g} = W\;yr\;m^{-2}K^{-1}$):',
                                  value=0.01, style=style, layout=layout)
tau_inp = widgets.FloatText(description='Ghost layer coupling timescale' + r'($\tau_{g}$):', value=1e-5, style=style, layout=layout)
years_inp = widgets.IntText(description='Duration in years:', value=30, style=style, layout=layout)
winter_inp = widgets.FloatText(description='time of coldest $T$:', value=26, style=style, layout=layout)
summer_inp = widgets.FloatText(description='time of warmest $T$:', value=76, style=style, layout=layout)

#news = widgets.Output(style={'description_width': '250px'}, layout={'width': '271px'})
reset_button_SeaIce = widgets.Button(description="Reset", style={'description_width': '250px'}, layout={'width': '250px'})
submit_button_SeaIce = widgets.Button(description="Submit", style={'description_width': '250px'}, layout={'width': '272px'})
info = widgets.Output(style=style, layout=layout)
output = widgets.Output()

def on_submit_clicked(b):
    info.clear_output()
    output.clear_output()
    
    x, xi, tfin, Tfin, Efin, Lf, winter, summer = calculationSeaIce(D_inp.value, S1_inp.value, A_inp.value, B_inp.value, cw_inp.value, S0_inp.value,
                      S2_inp.value, a0_inp.value, a2_inp.value, ai_inp.value, Fb_inp.value, k_inp.value,
                      Lf_inp.value, cg_inp.value, tau_inp.value, winter_inp.value, summer_inp.value, years_inp.value)
    
    f = plt.figure(figsize=(15, 10))
    
    with output:
        display(plot_SeaIce_result(x, xi, tfin, Tfin, Efin, Lf, winter, summer, f))
        
submit_button_SeaIce.on_click(on_submit_clicked)

def on_reset_clicked(b):
    D_inp.value=0.6
    S1_inp.value=338
    A_inp.value=193
    B_inp. value=2.1
    cw_inp.value=9.8
    S0_inp.value=420
    S2_inp.value=240
    a0_inp.value=0.7
    a2_inp.value=0.1
    ai_inp.value=0.4
    Fb_inp.value=4
    k_inp.value=2
    Lf_inp.value=9.5
    cg_inp.value=0.01
    tau_inp.value=1e-5
    years_inp.value=30
    winter_inp.value=26
    summer_inp.value=76
    
reset_button_SeaIce.on_click(on_reset_clicked)

SeaIceEBM_content = widgets.VBox([
    HBox([D_inp, A_inp]),
    HBox([S0_inp, B_inp]),
    HBox([S1_inp,cw_inp]),
    HBox([S2_inp, Fb_inp]),
    HBox([a0_inp, Lf_inp]),
    HBox([a2_inp, k_inp]),
    HBox([ai_inp, cg_inp]),
    HBox([winter_inp,tau_inp]),
    HBox([summer_inp, years_inp]),
    HBox([reset_button_SeaIce, submit_button_SeaIce, info]),
    output
])

# 4. Temperature EBM <a name="tebm"></a>
## 4.1 General <a name="generaltebm"></a>



## 4.2 Functions <a name="tebmfunctions"></a>

### Temperature EBM calculation

In [78]:
D=0.6; A=193; B=2.1; cw=9.8; S0=420; S2=240; a0=0.7; a2=0.1; ai=0.4; F=0.2
n = 50 # grid resolution (number of points between equator and pole)
nt = .5
dur = 100
dt = 1/nt
# Spatial Grid ---------------------------------------------------------
dx = 1.0/n # grid box width
x = np.arange(dx/2,1+dx/2,dx) #native grid
xb = np.arange(dx,1,dx)
# Diffusion Operator (WE15, Appendix A) -----------------------------------
lam = D/dx**2*(1-xb**2)
L1=np.append(0, -lam)
L2=np.append(-lam, 0)
L3=-L1-L2
diffop = - np.diag(L3) - np.diag(L2[:n-1],1) - np.diag(L1[1:n],-1);
S = S0-S2*x**2 # insolation [WE15 eq. (3) with S_1 = 0]
aw = a0-a2*x**2 # open water albedo

T = 10*np.ones(x.shape) # initial condition (constant temp. 10C everywhere)
allT = np.zeros([int(dur*nt),n])
t = np.linspace(0,dur,int(dur*nt))

I = np.identity(n)
invMat = np.linalg.inv(I+dt/cw*(B*I-diffop))
# integration over time using implicit difference and
# over x using central difference (through diffop)

for i in range(0,int(dur*nt)):
    a = aw*(T>0)+ai*(T<0) # WE15, eq.4
    C = a*S-A+F
    T0 = T+dt/cw*C
    # Governing equation [cf. WE15, eq. (2)]:
    # T(n+1) = T(n) + dt*(dT(n+1)/dt), with c_w*dT/dt=(C-B*T+diffop*T)
    # -> T(n+1) = T(n) + dt/cw*[C-B*T(n+1)+diff_op*T(n+1)]
    # -> T(n+1) = inv[1+dt/cw*(1+B-diff_op)]*(T(n)+dt/cw*C)
    T = np.dot(invMat,T0)
    allT[i,:]=T   
    

In [89]:
x = np.array([11,12])
y = np.array([40,80])
x*(y<50)

array([11,  0])

In [86]:
T

array([ 26.11878115,  26.08788242,  26.02607951,  25.93336145,
        25.80971147,  25.65510668,  25.46951759,  25.25290752,
        25.0052318 ,  24.72643693,  24.4164594 ,  24.07522446,
        23.70264456,  23.29861757,  22.8630247 ,  22.395728  ,
        21.89656756,  21.36535813,  20.80188513,  20.20590011,
        19.57711517,  18.91519656,  18.21975686,  17.49034579,
        16.72643907,  15.92742489,  15.09258752,  14.22108715,
        13.3119349 ,  12.36396168,  11.37577898,  10.34572888,
         9.27181974,   8.15164224,   6.98225845,   5.76005262,
         4.48052721,   3.13801818,   1.72528848,   0.23293206,
        -1.35152725,  -2.91982322,  -4.47294339,  -6.01183497,
        -7.53740679,  -9.05053121, -10.55204588, -12.04275536,
       -13.52343277, -14.99482122])

In [49]:
# to return multiple calculated values
class Result:
    def __init(self):
        self.empty = True
    def __init__(self, allT, t, T, x):
        self.allT = allT
        self.t = t
        self.T = T
        self.x = x
        self.empty = False

def calculationSimpleTEBM(D=0.6, A=193, B=2.1, cw=9.8, S0=420, S2=240, a0=0.7, a2=0.1, ai=0.4, F=0):
    n = 50 # grid resolution (number of points between equator and pole)
    nt = .5
    dur = 100
    dt = 1/nt
    # Spatial Grid ---------------------------------------------------------
    dx = 1.0/n # grid box width
    x = np.arange(dx/2,1+dx/2,dx) #native grid
    xb = np.arange(dx,1,dx)
    # Diffusion Operator (WE15, Appendix A) -----------------------------------
    lam = D/dx**2*(1-xb**2)
    L1=np.append(0, -lam)
    L2=np.append(-lam, 0)
    L3=-L1-L2
    diffop = - np.diag(L3) - np.diag(L2[:n-1],1) - np.diag(L1[1:n],-1);
    S = S0-S2*x**2 # insolation [WE15 eq. (3) with S_1 = 0]
    aw = a0-a2*x**2 # open water albedo

    T = 10*np.ones(x.shape) # initial condition (constant temp. 10C everywhere)
    allT = np.zeros([int(dur*nt),n])
    t = np.linspace(0,dur,int(dur*nt))

    I = np.identity(n)
    invMat = np.linalg.inv(I+dt/cw*(B*I-diffop))
    # integration over time using implicit difference and
    # over x using central difference (through diffop)

    for i in range(0,int(dur*nt)):
        a = aw*(T>0)+ai*(T<0) # WE15, eq.4
        C = a*S-A+F
        T0 = T+dt/cw*C
        # Governing equation [cf. WE15, eq. (2)]:
        # T(n+1) = T(n) + dt*(dT(n+1)/dt), with c_w*dT/dt=(C-B*T+diffop*T)
        # -> T(n+1) = T(n) + dt/cw*[C-B*T(n+1)+diff_op*T(n+1)]
        # -> T(n+1) = inv[1+dt/cw*(1+B-diff_op)]*(T(n)+dt/cw*C)
        T = np.dot(invMat,T0)
        allT[i,:]=T
    return Result(allT,t,T,x)    

### Temperature EBM plot function

In [50]:
def doit(diffusivity, olr_whenT_eq0, olr_temp_dependence, ocean_mixed_layer_heat_capacity,
         insolation_equator, insolation_spatial_dependence, ice_free_co_albedo_equtor, ice_fre_co_albedo_spatial_dependence,
         co_albedo_where_sea_ice, radioactive_forcing):  
    # -------------------------------------------------------------------------
    default_results = calculationSimpleTEBM()
    
    D = diffusivity # diffusivity for heat transport (W m^-2 K^-1)
    A = olr_whenT_eq0 # OLR when T = 0 (W m^-2)
    B = olr_temp_dependence # OLR temperature dependence (W m^-2 K^-1)
    cw = ocean_mixed_layer_heat_capacity # ocean mixed layer heat capacity (W yr m^-2 K^-1)
    S0 = insolation_equator # insolation at equator (W m^-2)
    S2 = insolation_spatial_dependence # insolation spatial dependence (W m^-2)
    a0 = ice_free_co_albedo_equtor # ice-free co-albedo at equator
    a2 = ice_fre_co_albedo_spatial_dependence # ice=free co-albedo spatial dependence
    ai = co_albedo_where_sea_ice # co-albedo where there is sea ice
    F = radioactive_forcing # radiative forcing (W m^-2)
    
    students_input_result = calculationSimpleTEBM(D, A, B, cw, S0, S2, a0, a2, ai, F)
    
    with sns.axes_style("whitegrid"):
        fig = plt.figure(figsize=(20,10))
        fig.suptitle('EBM_fast_WE15')
        plt.subplot(211)
        plt.plot(students_input_result.t, students_input_result.allT)
        plt.xlabel('t (years)')
        plt.ylabel('T (in $^\circ$C)')
        plt.subplot(212)

        plt.plot(np.concatenate([-np.flip(np.arcsin(default_results.x)*180/np.pi), np.arcsin(default_results.x)*180/np.pi]),
                 np.concatenate([np.flip(default_results.T), default_results.T]), label="default")

        xdeg = np.degrees(np.arcsin(default_results.x));

        if (students_input_result.allT == default_results.allT).all() and (students_input_result.T == default_results.T).all() and (students_input_result.t == default_results.t).all() and (students_input_result.x == default_results.x).all():  
            pass
        else:
            #plt.plot(np.arcsin(students_input_result.x)*180/np.pi, students_input_result.T, label="your input")
            plt.plot(np.concatenate([-np.flip(xdeg),xdeg]),#-np.flip(np.arcsin(students_input_result.x)*180/np.pi), np.arcsin(students_input_result.x)*180/np.pi]),
                    np.concatenate([np.flip(students_input_result.T), students_input_result.T]), label="your input")

        plt.xlabel('latitude'); plt.ylabel('T (in $^\circ$C)')
        plt.xticks(np.concatenate([-np.arange(len(students_input_result.x)*2),np.arange(len(students_input_result.x)*2)])[::10])
        plt.legend()
        
        for entry in range(len(saved_data)):
            if saved_data[entry]:
                #plt.plot(np.arcsin(saved_data[entry].x)*180/np.pi, saved_data[entry].T, label=str(entry+1)+". save")
                plt.plot(np.concatenate([-np.flip(np.arcsin(saved_data[entry].x)*180/np.pi), np.arcsin(saved_data[entry].x)*180/np.pi]),
                        np.concatenate([np.flip(saved_data[entry].T), saved_data[entry].T]), label=str(entry+1)+". save")
                plt.xlabel('latitude') 
                plt.ylabel('T (in $^\circ$C)')
                plt.legend()        

In [51]:
(180/np.pi)*np.arcsin(1)

90.0

### Temperature EBM widget settings

In [52]:
# save some settings
saved_data = np.empty(4, dtype=Result)

style = {'description_width': '260px'}
layout = {'width': '430px'}

# Model parameters (WE15, Table 1 and Section 2d) -------------------------
D_slider = widgets.FloatSlider(min=0, max=1, step=0.01,
                               description="Diffusivity:", value=0.6, style=style, layout=layout) # diffusivity for heat transport (W m^-2 K^-1)
A_slider = widgets.IntSlider(min=0, max=500, step=1,
                             description="OLR when T = 0:",value=193, style=style, layout=layout) #A = 193 # OLR when T = 0 (W m^-2)
B_slider = widgets.FloatSlider(min=0, max=10, step=0.1,
                               description="OLR temperature dependence:", value=2.1, style=style, layout=layout) #B = 2.1 # OLR temperature dependence (W m^-2 K^-1)
cw_slider = widgets.FloatSlider(min=0.001, max=50,
                                step=0.1, description="Ocean mixed layer heat capacity:", value=9.8, style=style, layout=layout) #cw = 9.8 # ocean mixed layer heat capacity (W yr m^-2 K^-1)
S0_slider = widgets.IntSlider(min=0, max=1000, step=1,
                              description="Insolation at equator:", value=420, style=style, layout=layout)  #S0 = 420 # insolation at equator (W m^-2)
S2_slider = widgets.IntSlider(min=0, max=1000, step=1,
                              description="Insolation spatial dependence:", value=240, style=style, layout=layout)  #S2 = 240 # insolation spatial dependence (W m^-2)
a0_slider = widgets.FloatSlider(min=0.001, max=1, step=0.05,
                                description="Ice-free coalbedo at equator:", value=0.7, style=style, layout=layout)  #a0 = 0.7 # ice-free co-albedo at equator
a2_slider = widgets.FloatSlider(min=0.001, max=1, step=0.05,
                                description="Ice-free coalbedo spatial dependence:", value=0.1, style=style, layout=layout)  #a2 = 0.1 # ice=free co-albedo spatial dependence
ai_slider = widgets.FloatSlider(min=0.001, max=1, step=0.05,
                                description="Coalbedo when there is sea ice:",value=0.4, style=style, layout=layout) #ai = 0.4 # co-albedo where there is sea ice
F_slider = widgets.FloatSlider(min=0, max=4, step=0.05,
                               description="Radioactive forcing:",value=0, style=style, layout=layout) #F = 0 # radiative forcing (W m^-2)
    
def reset_values(b):
    """Reset the interactive plots to inital values."""
    w1.children[0].value = 0.6; w1.children[1].value = 193; w1.children[2].value = 2.1
    w1.children[3].value = 9.8; w1.children[4].value = 420;  w1.children[5].value = 240
    w1.children[6].value = 0.7; w1.children[7].value = 0.1; w1.children[8].value = 0.4
    w1.children[9].value = 0

reset_button_TEBM = widgets.Button(description = "Reset")
reset_button_TEBM.on_click(reset_values)

w1=widgets.interactive(doit, diffusivity=D_slider, olr_whenT_eq0=A_slider, olr_temp_dependence=B_slider, ocean_mixed_layer_heat_capacity=cw_slider,
                       insolation_equator=S0_slider, insolation_spatial_dependence=S2_slider, ice_free_co_albedo_equtor=a0_slider,
                       ice_fre_co_albedo_spatial_dependence=a2_slider, co_albedo_where_sea_ice=ai_slider, radioactive_forcing=F_slider)

def refresh():
    w1.children[0].value = w1.children[0].value; w1.children[1].value = w1.children[1].value;
    w1.children[2].value = w1.children[2].value; w1.children[3].value = w1.children[3].value;
    w1.children[4].value += 1; w1.children[4].value -= 1; w1.children[5].value = w1.children[5].value;
    w1.children[6].value = w1.children[6].value; w1.children[7].value = w1.children[7].value;
    w1.children[8].value = w1.children[8].value; w1.children[9].value = w1.children[9].value
    
def saveData1(b):
    if not saved_data[0]:
        saved_data[0] = calculationSimpleTEBM(w1.children[0].value, w1.children[1].value, w1.children[2].value,
                                           w1.children[3].value, w1.children[4].value, w1.children[5].value,
                                           w1.children[6].value, w1.children[7].value, w1.children[8].value, w1.children[9].value)
    else: 
        saved_data[0] = None
        refresh()

        
def saveData2(b):
    if not saved_data[1]:
        saved_data[1] = calculationSimpleTEBM(w1.children[0].value, w1.children[1].value, w1.children[2].value,
                                           w1.children[3].value, w1.children[4].value, w1.children[5].value,
                                           w1.children[6].value, w1.children[7].value, w1.children[8].value, w1.children[9].value)
    else: 
        saved_data[1] = None
        refresh()
        
def saveData3(b):
    if not saved_data[2]:
        saved_data[2] = calculationSimpleTEBM(w1.children[0].value, w1.children[1].value, w1.children[2].value,
                                           w1.children[3].value, w1.children[4].value, w1.children[5].value,
                                           w1.children[6].value, w1.children[7].value, w1.children[8].value, w1.children[9].value)
    else: 
        saved_data[2] = None
        refresh()
        
def saveData4(b):
    if not saved_data[3]:
        saved_data[3] = calculationSimpleTEBM(w1.children[0].value, w1.children[1].value, w1.children[2].value,
                                           w1.children[3].value, w1.children[4].value, w1.children[5].value,
                                           w1.children[6].value, w1.children[7].value, w1.children[8].value, w1.children[9].value)
    else: 
        saved_data[3] = None
        refresh()
        
save1_button = widgets.Button(description="1. save / delete")
save1_button.on_click(saveData1)

save2_button = widgets.Button(description="2. save / delete")
save2_button.on_click(saveData2)

save3_button = widgets.Button(description="3. save / delete")
save3_button.on_click(saveData3)

save4_button = widgets.Button(description="4. save / delete")
save4_button.on_click(saveData4)

TEBM_content = widgets.Box(
        [VBox([
            VBox([
                HBox(w1.children[:-8]),
                HBox(w1.children[-8:-5]),
                HBox(w1.children[-5:-2]),
                HBox([
                    w1.children[-2],
                    HBox([reset_button_TEBM, save1_button, save2_button, save3_button, save4_button])])
            ]),
               w1.children[-1]
            ]
        )
        ]
    )

In [53]:
tab1 = SeaIceEBM_content
tab2 = TEBM_content

tab = widgets.Tab(children=[tab1, tab2])
tab.set_title(0, 'Sea Ice EBM')
tab.set_title(1, 'Temperaure EBM')

# 5. Try it out! <a name="widget"></a>

# <center> <<>>-------- SEA ICE and  Temperature - EBM --------<<>> </center>

> $x = 0$ latitude at the equator and $x = 1$ at the North Pole.

> $T_m$: melting temperature

> OLR: outgoing longwave radiation

> $S_O$: annual mean insolation at the equator

> $S^{*}_1$ : determines the amplitude of seasonal insolation variations ($\omega = 2\pi yr^{-1}$ is the annual frequency)

> $S_2$: determines the equator-to-pole insolation gradient

> Cloud cover and water vapor are not included in the sea ice model.

In [54]:
VBox(children=[tab])

Plot: Seasonal cycle of equilibrated climate (final year)

$a$.) $E(J\;m^{-2})$ shows seasonal cycle of surface enthalpy $E(t,x)$ which fully represents the model state since $E$ is the only prognostic variable in the forcing varies seasonally.

$b$.) Surface temperature $T(x,t)$ | $T(°C)$ 

$c$.) Sea ice thickness $h(x,t)$ | $h(m)$

$d$.) Surface temperature $T$ varies approcimately parabolic with x from equatorial $T$ with $30°C$ to a polar $T$ of $-10°C$ in winter and $-3°C$ in summer (with defualt parameters)

$e$.) Ice thickness $h$ in summer and winter where $x > 0.7$

$f$.) Seasonal cycle of ice thickness at the pole $h_p$ (default: $h_p \geq 3m$ at pole)

$g$.) Seasonal cycle of the latitude of sea ice edge $\theta_i$ (default: edge of the sea ice cover range from $\theta$ = $58°$ in winter to $76°$ in summer)

On default mode: 
- black curve in plot $a$ - $c$ indicates the ice edge

In [27]:
print(saved_data[0].x);print("\n")
print(np.degrees(np.arcsin(saved_data[0].x)))

AttributeError: 'NoneType' object has no attribute 'x'

In [ ]:
np.arange(0,50,2)

In [ ]:
#saved_data[0].t # time
#saved_data[0].T # Temperature 
#saved_data[0].x # location (0-1 equator-pole)
#saved_data[0].allT # all temperatures by latitude